<a href="https://colab.research.google.com/github/aman-17/actualwise/blob/main/old_actualwise_pipeline.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [20]:
# ! pip install pytesseract pdf2image
# ! pip install --upgrade git+https://github.com/huggingface/transformers
# ! pip install openai==0.28
! pip install torch

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 150.8/150.8 MB 1.7 MB/s eta 0:00:0000:0100:03
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 1.9 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.7/5.7 MB 2.7 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 536.2/536.2 kB 3.7 MB/s eta 0:00:00a 0:00:01


In [2]:
! mkdir 'casestudy1'
! mkdir 'casestudy2'
! mkdir 'casestudy3'
! mkdir 'images1'
! mkdir 'images2'
! mkdir 'images3'
! mkdir 'deid1'
! mkdir 'deid2'
! mkdir 'deid3'
! mkdir 'gpt4'
! mkdir 'summary'

mkdir: casestudy2: File exists


In [16]:
# Import the required function from the pdf2image library
from pdf2image import convert_from_path

# Use the convert_from_path function to convert the PDF file into a list of images
# Each page of the PDF is converted into a separate image
images = convert_from_path('Case_study_1_CO.pdf')

# Loop through the list of images
for i, image in enumerate(images):
    # Save each image as a PNG file
    # The file name includes the page number for easy identification
    image.save(f'images1/page_{i+1}.png', 'PNG')


In [17]:
# Import the required libraries
import os
import pytesseract
from PIL import Image

# Define a function to perform OCR on an image
def ocr_core(image):
    # Open the image file
    # Use pytesseract to convert the image into text
    text = pytesseract.image_to_string(Image.open(image))
    return text

# Define a function to extract text from all images in a folder
def extract_text_from_folder(folder_path):
    # Get a list of all files in the folder that end with .png or .jpg
    files = [f for f in os.listdir(folder_path) if f.endswith(".png") or f.endswith(".jpg")]
    # Sort files based on their numerical order
    files.sort(key=lambda x: int(x.split('_')[1].split('.')[0]))
    # Loop through the files
    for i in range(0, len(files), 1):
        # Define the output file path
        output_file = os.path.join(folder_path, f'output{i + 1}.txt')
        # Open the output file in write mode
        with open(output_file, 'w') as f:
            # Loop through the current file
            for filename in files[i:i+1]:
                # Define the image path
                image_path = os.path.join(folder_path, filename)
                # Extract text from the image
                text = ocr_core(image_path)
                # Write the extracted text to the output file
                f.write(f"{text}\n{'-'*30}\n")

# Define the folder path
folder_path = './images1'
# Call the function to extract text from all images in the folder
extract_text_from_folder(folder_path)


In [18]:
import os

# Define the directory containing the text files
directory = "images1"

# Loop through the text files in the directory
for filename in os.listdir(directory):
    if filename.endswith(".txt"):
        # Extract the page number from the filename
        page_number = filename.split('output')[1].split('.txt')[0]

        # Open the text file and read the text
        with open(os.path.join(directory, filename), 'r') as file:
            text = file.read()

        # Add the page number to the first line of the text
        text_with_page_number = f"Page Number {page_number}\n{text}"

        # Write the modified text back to the file
        with open(os.path.join(directory, filename), 'w') as file:
            file.write(text_with_page_number)


In [21]:
import os
import torch
from transformers import AutoTokenizer, AutoModelForMaskedLM, pipeline

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# Load the tokenizer and model from the pretrained "obi/deid_roberta_i2b2"
tokenizer = AutoTokenizer.from_pretrained("obi/deid_roberta_i2b2")
model = AutoModelForMaskedLM.from_pretrained("obi/deid_roberta_i2b2").to(device)
nlp = pipeline(task="ner", model="obi/deid_roberta_i2b2",device=0 if torch.cuda.is_available() else -1)

"""
tokenizer = AutoTokenizer.from_pretrained("nlpie/clinical-distilbert-i2b2-2010")
model = AutoModelForMaskedLM.from_pretrained("nlpie/clinical-distilbert-i2b2-2010").to(device)
nlp=pipeline(task="ner", model="obi/deid_bert_i2b2",device=0)
"""

# Define a function to deidentify text based on the NER results
def deidentify_text(text, ner_results):
    # Sort the entities based on their start position
    sorted_entities = sorted(ner_results, key=lambda x: x['start'])
    merged_entities = []

    # Merge overlapping entities
    for entity in sorted_entities:
        if merged_entities and entity['start'] <= merged_entities[-1]['end']:
            merged_entities[-1]['end'] = max(merged_entities[-1]['end'], entity['end'])
            merged_entities[-1]['entity'] = entity['entity']
        else:
            merged_entities.append(entity)

    # Replace the identified entities in the text with their entity type
    deidentified_text = text
    for entity in reversed(merged_entities):
        start = entity['start']
        end = entity['end']
        deidentified_text = deidentified_text[:start] + "[" + entity['entity'] + "]" + deidentified_text[end:]
    return deidentified_text

# Define the directory containing the text files
directory = "images1/"
# Define the directory to save the deidentified text files
new_directory = "deid1/"

# Loop through the text files in the directory
for filename in os.listdir(directory):
    if filename.endswith(".txt"):
        # Open the text file and read the text
        with open(os.path.join(directory, filename), 'r') as file:
            text = file.read()
            # Perform NER on the text
            ner_results = nlp(text)
            # Deidentify the text
            deidentified_text = deidentify_text(text, ner_results)
        # Write the deidentified text to a new file
        with open(os.path.join(new_directory, "deidentified_" + filename), 'w') as file:
            file.write(deidentified_text)


tokenizer_config.json:   0%|          | 0.00/351 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/798k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/2.50k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.42G [00:00<?, ?B/s]

Some weights of RobertaForMaskedLM were not initialized from the model checkpoint at obi/deid_roberta_i2b2 and are newly initialized: ['lm_head.bias', 'lm_head.decoder.bias', 'lm_head.dense.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.layer_norm.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Error during conversion: ValueError('Queue is full! Please try again.')
Error during conversion: ValueError('Queue is full! Please try again.')


model.safetensors:   0%|          | 0.00/1.42G [00:00<?, ?B/s]

In [23]:
import os

directory = "deid1"

# Get a list of all text files in the directory
files = [f for f in os.listdir(directory) if f.endswith(".txt")]

# Sort the files in ascending order of their numerical part
files.sort(key=lambda x: int(x.split('deidentified_output')[1].split('.txt')[0]))

# Create a new file to store the merged text
with open(os.path.join("./", "deidentification_output_merged.txt"), 'w') as outfile:
    for filename in files:
        # Open each text file and append its contents to the merged file
        with open(os.path.join(directory, filename), 'r') as infile:
            outfile.write(infile.read())
            # Add a newline character between files
            outfile.write("\n")

In [24]:
import os

# Define the path to your text file
file_path = "deidentification_output_merged.txt"

# Read the file
with open(file_path, 'r') as file:
    lines = file.readlines()

# Remove empty lines
new_lines = [line for line in lines if line.strip()]

# Write the modified lines back to the file
with open(file_path, 'w') as file:
    file.writelines(new_lines)


In [ ]:
import os
import openai
import json
import pandas as pd
from google.colab import userdata
gpt4_api = userdata.get('gpt4_api')

openai.api_type = "azure"
openai.api_key = gpt4_api
openai.api_base = "https://test-gpt-4-ks.openai.azure.com"
openai.api_version = "2023-05-15"
openai.log = "debug"

def chunk_text(text, chunk_size=8192):
    return [text[i:i+chunk_size] for i in range(0, len(text), chunk_size)]

def process_file(file_path):
    with open(file_path, 'r') as file:
        text = file.read()
    df = pd.read_excel('/content/ChatGPT prompts v5.xlsx',sheet_name=1)
    questions = df['Rafi\'s Qs'].tolist()
    chunks = chunk_text(text)
    messages = [
        # {
        #     "role": "system",
        #     "content": "You are a helpful assistant."
        # },
    ]
    for question in questions:
        for chunk in chunks:
            if len(chunk) > 8192:
                print(f"Warning: chunk is too large ({len(chunk)} tokens)")
                continue
            messages.append({
                "role": "user",
                "content": chunk + question
            })
        print(question)
    return messages

def get_responses(messages):
    responses = []
    for message in messages:
        response = openai.ChatCompletion.create(
            deployment_id="test",
            messages=[message],
        )
        responses.append(response["choices"][0]["message"]["content"])
    return responses

def save_responses_to_file(responses, output_file):
    with open(output_file, 'w') as f:
        for response in responses:
            f.write(f"{response}\n{'-'*30}\n")

def process_files_in_folder(folder_path):
    files = [f for f in os.listdir(folder_path) if f.endswith(".txt")]
    for filename in files:
        file_path = os.path.join(folder_path, filename)
        output_file = os.path.join(folder_path, f'output_{filename}')
        messages = process_file(file_path)
        responses = get_responses(messages)
        for response in responses:
            print(response)

        # print(print(responses["choices"][0]["message"]["content"]))

folder_path = '/content/'
process_files_in_folder(folder_path)


Does the patient have or are they taking any prescription drugs that indicate they have Carbapenem-resistant Enterobacteriaceae (CRE) or bacteria that are resistant to carbapenem antibiotics? Respond concisely "CRE: Yes" or "CRE: No". For 'Yes' responses, include the page number(s) indicating the source, for example "Page 1" or "Pages 1,2,3". Omit any summary statements before or after the response.
Does the patient have or are they taking any prescription drugs that indicate they have Candida Auris (C-Auris) which is resistant to multiple antifungal drugs?  Respond concisely "C-Auris: Yes" or "C-Auris: No". For 'Yes' responses, include the page number(s) indicating the source, for example "Page 1" or "Pages 1,2,3". Omit any summary statements before or after the response.
Does the patient have or are they taking any prescription drugs that indicate they have Methicillin-Resist ant Staphylococcus Aureus (MRSA) which is resistant to many antibiotics used to treat common staph infections

message='Request to OpenAI API' method=post path=https://test-gpt-4-ks.openai.azure.com/openai/deployments/test/chat/completions?api-version=2023-05-15
api_version=2023-05-15 data='{"messages": [{"role": "user", "content": "Page Number 1\\nPowered by [U-PATORG]GoldFax [L-DATE] 14:30 [U-HOSP]GoldFax Page [U-DATE]28\\nMedication Administration Record\\n[L-DATE] 11:00 - [L-DATE] 12:37\\n\\u2018Name:\\nLocation:\\nPhysician: [I-STAFF] [L-STAFF] \\nD Blood Glucose Monitoring\\nNOW\\nD Care Profile and Crisis Plan\\nEVERY 4 HOURS - UNTIL COMPLETE\\nD CBC W/O DIFFERENTIAL,\\nEVERY MORNING UNTIL COMPLETE\\nD COMPREHENSIVE METABOLIC\\nEVERY MORNING UNTIL COMPLETE\\nD Consent and Declination of Seasonal Influenza\\nVaccine\\nEVERY 12 HOURS UNTIL COMPLETE\\n\\u2018A COWS Scale\\nEvery 4 hours - COWS\\nFF initial score 10 assess vitals per protocolVerify\\nwith MD the initiation of the medical detox\\nprotocol.\\n\\u2018A Daily Nursing Progress Note\\nTwice a Day Assessments\\n\\u2018Stack: 11:42 

CRE: No
CRE: No
CRE: No
CRE: No
CRE: No
C-Auris: No
C-Auris: No
C-Auris: No
C-Auris: No
C-Auris: No
MRSA: No
MRSA: No
MRSA: No
MRSA: No
MRSA: No
C-DIFF: No
C-DIFF: No
C-DIFF: No
C-DIFF: No
C-DIFF: No
MDRO: No
MDRO: No
The text provided does not mention any instance of the patient having a Multidrug-Resistant Organism (MDRO). Therefore, the concise response would be "MDRO: No".
MDRO: No
MDRO: No
COVID: No
COVID: No
COVID: No
COVID: No
COVID: No
A&OxNA
A&OxNA
A&OxNA
The patient is oriented to Place, Person, and Situation (A&Ox3) as indicated on Page 6.
A&OxNA
COVID vaccination: NA
COVID vaccination: No
COVID vaccination: NA
COVID vaccination: NA
COVID vaccination: NA
COVID test: NA
COVID test: NA
COVID test: NA
COVID test: NA
COVID test: NA
No short-term care plan mentioned.
No short-term care plan mentioned.
No short-term care plan mentioned.
No short-term care plan mentioned.
- Living/Placement Home/independent Living, Residential [I-HOSP] Center and [I-HOSP] [L-HOSP]/Shelter
- Partial

message='OpenAI API response' path=https://test-gpt-4-ks.openai.azure.com/openai/deployments/test/chat/completions?api-version=2023-05-15 processing_ms=None request_id=3c088655-ccd2-419b-a0cb-2b290dae37dd response_code=200
body='{"id":"chatcmpl-8sdyJEYAUrgTTqKpnADZnJjNZSGRS","object":"chat.completion","created":1708034055,"model":"gpt-4","choices":[{"finish_reason":"stop","index":0,"message":{"role":"assistant","content":"NA"}}],"usage":{"prompt_tokens":1693,"completion_tokens":1,"total_tokens":1694}}\n' headers="{'Cache-Control': 'no-cache, must-revalidate', 'Content-Length': '278', 'Content-Type': 'application/json', 'access-control-allow-origin': '*', 'apim-request-id': '103d9132-7aca-4c6e-a5ce-619f51d54d29', 'Strict-Transport-Security': 'max-age=31536000; includeSubDomains; preload', 'x-content-type-options': 'nosniff', 'x-ms-region': 'Canada East', 'x-ratelimit-remaining-requests': '6', 'x-ratelimit-remaining-tokens': '19104', 'x-accel-buffering': 'no', 'x-request-id': '3c088655-c

In [ ]:
# ignore for now
from paddleocr import PaddleOCR, draw_ocr


ocr = PaddleOCR(use_angle_cls=True, lang="en", page_num=2)
img_path = '/content/Case_study_1_CO.pdf'
result = ocr.ocr(img_path, cls=True)
for idx in range(len(result)):
    res = result[idx]
    for line in res:
        print(line)

# draw result
import fitz
from PIL import Image
import cv2
import numpy as np
imgs = []
with fitz.open(img_path) as pdf:
    for pg in range(0, pdf.pageCount):
        page = pdf[pg]
        mat = fitz.Matrix(2, 2)
        pm = page.getPixmap(matrix=mat, alpha=False)
        if pm.width > 2000 or pm.height > 2000:
            pm = page.getPixmap(matrix=fitz.Matrix(1, 1), alpha=False)

        img = Image.frombytes("RGB", [pm.width, pm.height], pm.samples)
        img = cv2.cvtColor(np.array(img), cv2.COLOR_RGB2BGR)
        imgs.append(img)
for idx in range(len(result)):
    res = result[idx]
    image = imgs[idx]
    boxes = [line[0] for line in res]
    txts = [line[1][0] for line in res]
    scores = [line[1][1] for line in res]
    im_show = draw_ocr(image, boxes, txts, scores, font_path='doc/fonts/simfang.ttf')
    im_show = Image.fromarray(im_show)
    im_show.save('result_page_{}.jpg'.format(idx))